In [69]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
from dateutil import parser
import datetime as dt
import duckdb as db
import plotly as ply
import plotly.express as px
from geopy.geocoders import Nominatim


In [70]:
covid_data = pd.read_csv ('covid_19_indonesia_time_series_all.csv')
pd.set_option ('display.max_columns', None)
covid_data.head()

Date Location ISO Code     Location  New Cases  New Deaths  \
0  3/1/2020             ID-JK  DKI Jakarta          2           0   
1  3/2/2020             ID-JK  DKI Jakarta          2           0   
2  3/2/2020               IDN    Indonesia          2           0   
3  3/2/2020             ID-RI         Riau          1           0   
4  3/3/2020             ID-JK  DKI Jakarta          2           0   

   New Recovered  New Active Cases  Total Cases  Total Deaths  \
0              0                 2           39            20   
1              0                 2           41            20   
2              0                 2            2             0   
3              0                 1            1             0   
4              0                 2           43            20   

   Total Recovered  Total Active Cases Location Level  City or Regency  \
0               75                 -56       Province              NaN   
1               75                 -54       Province              NaN   
2                0                   2        Country              NaN   
3                1                   0       Province              NaN   
4               75                 -52       Province              NaN   

      Province    Country Continent    Island  Time Zone  \
0  DKI Jakarta  Indonesia      Asia      Jawa  UTC+07:00   
1  DKI Jakarta  Indonesia      Asia      Jawa  UTC+07:00   
2          NaN  Indonesia      Asia       NaN        NaN   
3         Riau  Indonesia      Asia  Sumatera  UTC+07:00   
4  DKI Jakarta  Indonesia      Asia      Jawa  UTC+07:00   

           Special Status  Total Regencies  Total Cities  Total Districts  \
0  Daerah Khusus Ibu Kota                1           5.0               44   
1  Daerah Khusus Ibu Kota                1           5.0               44   
2                     NaN              416          98.0             7230   
3                     NaN               10           2.0              169   
4  Daerah Khusus Ibu Kota                1           5.0               44   

   Total Urban Villages  Total Rural Villages  Area (km2)  Population  \
0                 267.0                   NaN         664    10846145   
1                 267.0                   NaN         664    10846145   
2                8488.0               74953.0     1916907   265185520   
3                 268.0                1591.0       87024     6074100   
4                 267.0                   NaN         664    10846145   

   Population Density   Longitude  Latitude  New Cases per Million  \
0            16334.31  106.836118 -6.204699                   0.18   
1            16334.31  106.836118 -6.204699                   0.18   
2              138.34  113.921327 -0.789275                   0.01   
3               69.80  101.805109  0.511648                   0.16   
4            16334.31  106.836118 -6.204699                   0.18   

   Total Cases per Million  New Deaths per Million  Total Deaths per Million  \
0                     3.60                     0.0                      1.84   
1                     3.78                     0.0                      1.84   
2                     0.01                     0.0                      0.00   
3                     0.16                     0.0                      0.00   
4                     3.96                     0.0                      1.84   

   Total Deaths per 100rb Case Fatality Rate Case Recovered Rate  \
0                    0.18             51.28%             192.31%   
1                    0.18             48.78%             182.93%   
2                    0.00              0.00%               0.00%   
3                    0.00              0.00%             100.00%   
4                    0.18             46.51%             174.42%   

   Growth Factor of New Cases  Growth Factor of New Deaths  
0                         NaN                          NaN  
1                         1.0                          1.0  

In [71]:
def query (sql_query:str):
    return db.sql(sql_query).df()

In [72]:
covid_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 31822 entries, 0 to 31821
Data columns (total 38 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   Date                         31822 non-null  object 
 1   Location ISO Code            31822 non-null  object 
 2   Location                     31822 non-null  object 
 3   New Cases                    31822 non-null  int64  
 4   New Deaths                   31822 non-null  int64  
 5   New Recovered                31822 non-null  int64  
 6   New Active Cases             31822 non-null  int64  
 7   Total Cases                  31822 non-null  int64  
 8   Total Deaths                 31822 non-null  int64  
 9   Total Recovered              31822 non-null  int64  
 10  Total Active Cases           31822 non-null  int64  
 11  Location Level               31822 non-null  object 
 12  City or Regency              0 non-null      float64
 13  Province        

In [73]:
## merubah data type 
covid_data ['Date'] = covid_data ['Date'].map(parser.parse)
covid_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 31822 entries, 0 to 31821
Data columns (total 38 columns):
 #   Column                       Non-Null Count  Dtype         
---  ------                       --------------  -----         
 0   Date                         31822 non-null  datetime64[ns]
 1   Location ISO Code            31822 non-null  object        
 2   Location                     31822 non-null  object        
 3   New Cases                    31822 non-null  int64         
 4   New Deaths                   31822 non-null  int64         
 5   New Recovered                31822 non-null  int64         
 6   New Active Cases             31822 non-null  int64         
 7   Total Cases                  31822 non-null  int64         
 8   Total Deaths                 31822 non-null  int64         
 9   Total Recovered              31822 non-null  int64         
 10  Total Active Cases           31822 non-null  int64         
 11  Location Level               31822 non-nu

In [74]:
covid_data.loc[1000].to_dict()

{'Date': Timestamp('2020-04-18 00:00:00'),
 'Location ISO Code': 'ID-KB',
 'Location': 'Kalimantan Barat',
 'New Cases': 0,
 'New Deaths': 0,
 'New Recovered': 0,
 'New Active Cases': 0,
 'Total Cases': 21,
 'Total Deaths': 3,
 'Total Recovered': 6,
 'Total Active Cases': 12,
 'Location Level': 'Province',
 'City or Regency': nan,
 'Province': 'Kalimantan Barat',
 'Country': 'Indonesia',
 'Continent': 'Asia',
 'Island': 'Kalimantan',
 'Time Zone': 'UTC+07:00',
 'Special Status': nan,
 'Total Regencies': 12,
 'Total Cities': 2.0,
 'Total Districts': 174,
 'Total Urban Villages': 99.0,
 'Total Rural Villages': 2031.0,
 'Area (km2)': 147307,
 'Population': 5422814,
 'Population Density': 36.81,
 'Longitude': 111.1211776,
 'Latitude': -0.086474572,
 'New Cases per Million': 0.0,
 'Total Cases per Million': 3.87,
 'New Deaths per Million': 0.0,
 'Total Deaths per Million': 0.55,
 'Total Deaths per 100rb': 0.06,
 'Case Fatality Rate': '14.29%',
 'Case Recovered Rate': '28.57%',
 'Growth Fact

In [75]:
covid_data.loc[1000].to_dict()

{'Date': Timestamp('2020-04-18 00:00:00'),
 'Location ISO Code': 'ID-KB',
 'Location': 'Kalimantan Barat',
 'New Cases': 0,
 'New Deaths': 0,
 'New Recovered': 0,
 'New Active Cases': 0,
 'Total Cases': 21,
 'Total Deaths': 3,
 'Total Recovered': 6,
 'Total Active Cases': 12,
 'Location Level': 'Province',
 'City or Regency': nan,
 'Province': 'Kalimantan Barat',
 'Country': 'Indonesia',
 'Continent': 'Asia',
 'Island': 'Kalimantan',
 'Time Zone': 'UTC+07:00',
 'Special Status': nan,
 'Total Regencies': 12,
 'Total Cities': 2.0,
 'Total Districts': 174,
 'Total Urban Villages': 99.0,
 'Total Rural Villages': 2031.0,
 'Area (km2)': 147307,
 'Population': 5422814,
 'Population Density': 36.81,
 'Longitude': 111.1211776,
 'Latitude': -0.086474572,
 'New Cases per Million': 0.0,
 'Total Cases per Million': 3.87,
 'New Deaths per Million': 0.0,
 'Total Deaths per Million': 0.55,
 'Total Deaths per 100rb': 0.06,
 'Case Fatality Rate': '14.29%',
 'Case Recovered Rate': '28.57%',
 'Growth Fact

In [76]:
coord = covid_data ['Latitude'] [1000], covid_data ['Longitude'] [1000]
coordinate = f'{coord[0]},{coord[1]}'
coordinate

'-0.086474572,111.1211776'

In [77]:
geolocator = Nominatim(user_agent="DataAnalyst") 
location= geolocator.reverse(coordinate)
location.raw

{'place_id': 61825482,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. http://osm.org/copyright',
 'osm_type': 'node',
 'osm_id': 1308617863,
 'lat': '-0.0575879',
 'lon': '111.1028351',
 'class': 'place',
 'type': 'village',
 'place_rank': 19,
 'importance': 0.27501,
 'addresstype': 'village',
 'name': 'Engkersik',
 'display_name': 'Engkersik, Sekadau Hilir, Sekadau, Kalimantan Barat, Kalimantan, Indonesia',
 'address': {'village': 'Engkersik',
  'town': 'Sekadau Hilir',
  'county': 'Sekadau',
  'state': 'Kalimantan Barat',
  'ISO3166-2-lvl4': 'ID-KB',
  'region': 'Kalimantan',
  'ISO3166-2-lvl3': 'ID-KA',
  'country': 'Indonesia',
  'country_code': 'id'},
 'boundingbox': ['-0.0775879', '-0.0375879', '111.0828351', '111.1228351']}

In [78]:
print (location)
print (type(location))

Engkersik, Sekadau Hilir, Sekadau, Kalimantan Barat, Kalimantan, Indonesia
<class 'geopy.location.Location'>


In [79]:
def search_city (latitude:float, longitude:float)-> str:
    geolocator = Nominatim(user_agent="DataAnalyst", timeout=5)
    coordinates = f'{latitude}, {longitude}'
    location = geolocator.reverse(coordinates)
    return location.raw.get('address',{}).get('county','')

In [80]:
print (search_city(-0.086474572,111.1211776))

Sekadau


In [81]:
null_city_regency = list(covid_data[['Latitude', 'Longitude']].values)
counter = 1
city_code = {}

for counter, location in enumerate(null_city_regency, start=1):
    location_key = f'{location[0]}/{location[1]}'
    if location_key not in city_code:
        city = search_city(location[0], location[1])
        city_code[location_key] = city
    print(f"Detection location {counter} for {location} -> {city_code[location_key]}")
    counter+=1


Detection location 1 for [ -6.20469899 106.8361183 ] -> 
Detection location 2 for [ -6.20469899 106.8361183 ] -> 
Detection location 3 for [ -0.789275 113.921327] -> Kapuas
Detection location 4 for [  0.51164785 101.8051092 ] -> Siak
Detection location 5 for [ -6.20469899 106.8361183 ] -> 
Detection location 6 for [ -0.789275 113.921327] -> Kapuas
Detection location 7 for [ -6.92043208 107.6037083 ] -> 
Detection location 8 for [  0.51164785 101.8051092 ] -> Siak
Detection location 9 for [ -6.20469899 106.8361183 ] -> 
Detection location 10 for [ -0.789275 113.921327] -> Kapuas
Detection location 11 for [ -6.92043208 107.6037083 ] -> 
Detection location 12 for [  0.51164785 101.8051092 ] -> Siak
Detection location 13 for [ -6.20469899 106.8361183 ] -> 
Detection location 14 for [ -0.789275 113.921327] -> Kapuas
Detection location 15 for [ -6.92043208 107.6037083 ] -> 
Detection location 16 for [  0.51164785 101.8051092 ] -> Siak
Detection location 17 for [ -6.45673639 106.1090043 ] -> 

In [82]:
def search_city2 (latitude:float, longitude:float)-> str:
    geolocator = Nominatim(user_agent="DataAnalyst", timeout=5)
    coordinates = f'{latitude}, {longitude}'
    location = geolocator.reverse(coordinates)
    return location.raw.get('address',{}).get('county','')

In [83]:
null_city_regency = list(covid_data[['Latitude', 'Longitude']].values)
counter = 1
city_code = {}

for counter, location in enumerate(null_city_regency, start=1):
    location_key = f'{location[0]}/{location[1]}'
    if location_key not in city_code:
        city = search_city2(location[0], location[1])
        city_code[location_key] = city
    print(f"Detection location {counter} for {location} -> {city_code[location_key]}")
    counter+=1


Detection location 1 for [ -6.20469899 106.8361183 ] -> 
Detection location 2 for [ -6.20469899 106.8361183 ] -> 
Detection location 3 for [ -0.789275 113.921327] -> Kapuas
Detection location 4 for [  0.51164785 101.8051092 ] -> Siak
Detection location 5 for [ -6.20469899 106.8361183 ] -> 
Detection location 6 for [ -0.789275 113.921327] -> Kapuas
Detection location 7 for [ -6.92043208 107.6037083 ] -> 
Detection location 8 for [  0.51164785 101.8051092 ] -> Siak
Detection location 9 for [ -6.20469899 106.8361183 ] -> 
Detection location 10 for [ -0.789275 113.921327] -> Kapuas
Detection location 11 for [ -6.92043208 107.6037083 ] -> 
Detection location 12 for [  0.51164785 101.8051092 ] -> Siak
Detection location 13 for [ -6.20469899 106.8361183 ] -> 
Detection location 14 for [ -0.789275 113.921327] -> Kapuas
Detection location 15 for [ -6.92043208 107.6037083 ] -> 
Detection location 16 for [  0.51164785 101.8051092 ] -> Siak
Detection location 17 for [ -6.45673639 106.1090043 ] -> 

In [84]:
import json

In [85]:
with open("city_code.json", "w") as outfile:
    json.dump(city_code, outfile, indent=4)

In [86]:
with open("city_code1.json", "r") as my_city:
    city_code =json.load(my_city)
city_code

{'-6.204698991/106.8361183': 'Jakarta Pusat',
 '-0.789275/113.921327': 'Kapuas',
 '0.511647851/101.8051092': 'Siak',
 '-6.920432083/107.6037083': 'Kota Bandung,',
 '-6.456736388/106.1090043': 'Lebak',
 '-7.259097177/110.2011149': 'Temanggung',
 '-4.124688793/122.070311': 'Konawe Selatan',
 '-8.369471688/115.1317136': 'Tabanan',
 '0.45385803/116.4684405': 'Kutai Timur',
 '-7.89450185/110.4448783': 'Bantul',
 '2.191894453/99.05196442': 'Tapanuli Utara',
 '-7.723345579/112.7329414': 'Pasuruan',
 '3.916346/108.261746': 'Natuna',
 '-3.731080714/120.1620559': 'Sulawesi Utara',
 '-1.69769766/102.7236404': 'Tebo',
 '-3.192572/129.576792': 'Maluku Tengah',
 '-4.66620953/138.69603': 'Nduga',
 '0.212036949/127.5391072': 'Maluku Utara',
 '-3.216211808/104.1694647': 'Penukal Abab Lematang Ilir',
 '4.225614628/96.91052174': 'Aceh Tengah',
 '-1.602484653/113.4176536': 'Katingan',
 '-4.916792975/105.0214366': 'Lampung Utara',
 '-1.00413668/121.2010927': 'Sulawesi Tengah',
 '1.259638212/124.5212396': '

In [87]:
covid_data['City or Regency'] = covid_data.apply(
    lambda rows: city_code.get(f"{rows['Latitude']}/{rows['Longitude']}", None) if pd.isna(rows["City or Regency"]) else rows["City or Regency"],
    axis=1)

In [88]:
covid_data.head()

Date Location ISO Code     Location  New Cases  New Deaths  \
0 2020-03-01             ID-JK  DKI Jakarta          2           0   
1 2020-03-02             ID-JK  DKI Jakarta          2           0   
2 2020-03-02               IDN    Indonesia          2           0   
3 2020-03-02             ID-RI         Riau          1           0   
4 2020-03-03             ID-JK  DKI Jakarta          2           0   

   New Recovered  New Active Cases  Total Cases  Total Deaths  \
0              0                 2           39            20   
1              0                 2           41            20   
2              0                 2            2             0   
3              0                 1            1             0   
4              0                 2           43            20   

   Total Recovered  Total Active Cases Location Level City or Regency  \
0               75                 -56       Province   Jakarta Pusat   
1               75                 -54       Province   Jakarta Pusat   
2                0                   2        Country          Kapuas   
3                1                   0       Province            Siak   
4               75                 -52       Province   Jakarta Pusat   

      Province    Country Continent    Island  Time Zone  \
0  DKI Jakarta  Indonesia      Asia      Jawa  UTC+07:00   
1  DKI Jakarta  Indonesia      Asia      Jawa  UTC+07:00   
2          NaN  Indonesia      Asia       NaN        NaN   
3         Riau  Indonesia      Asia  Sumatera  UTC+07:00   
4  DKI Jakarta  Indonesia      Asia      Jawa  UTC+07:00   

           Special Status  Total Regencies  Total Cities  Total Districts  \
0  Daerah Khusus Ibu Kota                1           5.0               44   
1  Daerah Khusus Ibu Kota                1           5.0               44   
2                     NaN              416          98.0             7230   
3                     NaN               10           2.0              169   
4  Daerah Khusus Ibu Kota                1           5.0               44   

   Total Urban Villages  Total Rural Villages  Area (km2)  Population  \
0                 267.0                   NaN         664    10846145   
1                 267.0                   NaN         664    10846145   
2                8488.0               74953.0     1916907   265185520   
3                 268.0                1591.0       87024     6074100   
4                 267.0                   NaN         664    10846145   

   Population Density   Longitude  Latitude  New Cases per Million  \
0            16334.31  106.836118 -6.204699                   0.18   
1            16334.31  106.836118 -6.204699                   0.18   
2              138.34  113.921327 -0.789275                   0.01   
3               69.80  101.805109  0.511648                   0.16   
4            16334.31  106.836118 -6.204699                   0.18   

   Total Cases per Million  New Deaths per Million  Total Deaths per Million  \
0                     3.60                     0.0                      1.84   
1                     3.78                     0.0                      1.84   
2                     0.01                     0.0                      0.00   
3                     0.16                     0.0                      0.00   
4                     3.96                     0.0                      1.84   

   Total Deaths per 100rb Case Fatality Rate Case Recovered Rate  \
0                    0.18             51.28%             192.31%   
1                    0.18             48.78%             182.93%   
2                    0.00              0.00%               0.00%   
3                    0.00              0.00%             100.00%   
4                    0.18             46.51%             174.42%   

   Growth Factor of New Cases  Growth Factor of New Deaths  
0                         NaN                          NaN  
1                         1.0                          1.0  


In [89]:
kejadian_dipulau = covid_data.groupby('Island')['Total Cases'].sum()
kejadian_dipulau

Island
Jawa             1684649515
Kalimantan        196760968
Maluku             15828640
Nusa Tenggara     116845418
Papua              35920096
Sulawesi          138687078
Sumatera          345841842
Name: Total Cases, dtype: int64

In [90]:
value_counts = covid_data.groupby('Island')['Total Cases'].sum()
print(value_counts)

explode = [0.08, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
list_value = list(value_counts.values)
list_label = list(value_counts.index)

print(list_value)
print(list_label)

Island
Jawa             1684649515
Kalimantan        196760968
Maluku             15828640
Nusa Tenggara     116845418
Papua              35920096
Sulawesi          138687078
Sumatera          345841842
Name: Total Cases, dtype: int64
[1684649515, 196760968, 15828640, 116845418, 35920096, 138687078, 345841842]
['Jawa', 'Kalimantan', 'Maluku', 'Nusa Tenggara', 'Papua', 'Sulawesi', 'Sumatera']


In [91]:
# menampilkan total kasus diberbagai pulau

fig = ply.graph_objs.Figure (
  data=[
       ply.graph_objs.Pie(labels=list_label, values= list_value, pull=explode)]
       )
fig.update_layout (title_text='TOTAL CASE COVID DI INDONESIA')
fig.show()

In [128]:
jawa = query("SELECT * FROM covid_data where Island ='Jawa'")
jawa.head()

Date Location ISO Code     Location  New Cases  New Deaths  \
0 2020-03-01             ID-JK  DKI Jakarta          2           0   
1 2020-03-02             ID-JK  DKI Jakarta          2           0   
2 2020-03-03             ID-JK  DKI Jakarta          2           0   
3 2020-03-03             ID-JB   Jawa Barat          1           1   
4 2020-03-04             ID-JK  DKI Jakarta          2           0   

   New Recovered  New Active Cases  Total Cases  Total Deaths  \
0              0                 2           39            20   
1              0                 2           41            20   
2              0                 2           43            20   
3              0                 0            1             1   
4              0                 2           45            20   

   Total Recovered  Total Active Cases Location Level City or Regency  \
0               75                 -56       Province   Jakarta Pusat   
1               75                 -54       Province   Jakarta Pusat   
2               75                 -52       Province   Jakarta Pusat   
3               60                 -60       Province   Kota Bandung,   
4               75                 -50       Province   Jakarta Pusat   

      Province    Country Continent Island  Time Zone          Special Status  \
0  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   
1  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   
2  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   
3   Jawa Barat  Indonesia      Asia   Jawa  UTC+07:00                    None   
4  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   

   Total Regencies  Total Cities  Total Districts  Total Urban Villages  \
0                1           5.0               44                 267.0   
1                1           5.0               44                 267.0   
2                1           5.0               44                 267.0   
3               18           9.0              627                 645.0   
4                1           5.0               44                 267.0   

   Total Rural Villages  Area (km2)  Population  Population Density  \
0                   NaN         664    10846145            16334.31   
1                   NaN         664    10846145            16334.31   
2                   NaN         664    10846145            16334.31   
3                5312.0       35378    45161325             1276.55   
4                   NaN         664    10846145            16334.31   

    Longitude  Latitude  New Cases per Million  Total Cases per Million  \
0  106.836118 -6.204699                   0.18                     3.60   
1  106.836118 -6.204699                   0.18                     3.78   
2  106.836118 -6.204699                   0.18                     3.96   
3  107.603708 -6.920432                   0.02                     0.02   
4  106.836118 -6.204699                   0.18                     4.15   

   New Deaths per Million  Total Deaths per Million  Total Deaths per 100rb  \
0                    0.00                      1.84                    0.18   
1                    0.00                      1.84                    0.18   
2                    0.00                      1.84                    0.18   
3                    0.02                      0.02                    0.00   
4                    0.00                      1.84                    0.18   

  Case Fatality Rate Case Recovered Rate  Growth Factor of New Cases  \
0             51.28%             192.31%                         NaN   
1             48.78%             182.93%                         1.0   
2             46.51%             174.42%                         1.0   
3            100.00%            6000.00%                         NaN   
4             44.44%             166.67%                         1.0   

   Growth Factor of New Deaths  


In [129]:
Pulau_jawa = jawa.groupby ('City or Regency')['Total Cases'].sum()
Pulau_jawa

City or Regency
Bantul            86090207
Jakarta Pusat    545806047
Kota Bandung,    439196053
Lebak            100598017
Pasuruan         239912685
Temanggung       273046506
Name: Total Cases, dtype: int64

In [130]:
Pulau_jawa_Grup = jawa.groupby ('City or Regency')['Total Cases'].sum()
print(Pulau_jawa_Grup)

explode = [0.08, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
list_value1 = list(Pulau_jawa_Grup.values)
list_label1 = list(Pulau_jawa_Grup.index)

print(list_value1)
print(list_label1)

City or Regency
Bantul            86090207
Jakarta Pusat    545806047
Kota Bandung,    439196053
Lebak            100598017
Pasuruan         239912685
Temanggung       273046506
Name: Total Cases, dtype: int64
[86090207, 545806047, 439196053, 100598017, 239912685, 273046506]
['Bantul', 'Jakarta Pusat', 'Kota Bandung,', 'Lebak', 'Pasuruan', 'Temanggung']


In [95]:
# menampilkan total kasus diberbagai pulau

fig = ply.graph_objs.Figure (
  data=[
       ply.graph_objs.Pie(labels=list_label1, values= list_value1, pull=explode)]
       )
fig.update_layout (title_text='TOTAL CASE COVID DI PULAU JAWA')
fig.show()

In [120]:
jakarta = jawa [jawa ['City or Regency'] == 'Jakarta Pusat']
jakarta.head()

Date Location ISO Code     Location  New Cases  New Deaths  \
0 2020-03-01             ID-JK  DKI Jakarta          2           0   
1 2020-03-02             ID-JK  DKI Jakarta          2           0   
2 2020-03-03             ID-JK  DKI Jakarta          2           0   
4 2020-03-04             ID-JK  DKI Jakarta          2           0   
6 2020-03-05             ID-JK  DKI Jakarta          0           1   

   New Recovered  New Active Cases  Total Cases  Total Deaths  \
0              0                 2           39            20   
1              0                 2           41            20   
2              0                 2           43            20   
4              0                 2           45            20   
6              0                -1           45            21   

   Total Recovered  Total Active Cases Location Level City or Regency  \
0               75                 -56       Province   Jakarta Pusat   
1               75                 -54       Province   Jakarta Pusat   
2               75                 -52       Province   Jakarta Pusat   
4               75                 -50       Province   Jakarta Pusat   
6               75                 -51       Province   Jakarta Pusat   

      Province    Country Continent Island  Time Zone          Special Status  \
0  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   
1  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   
2  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   
4  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   
6  DKI Jakarta  Indonesia      Asia   Jawa  UTC+07:00  Daerah Khusus Ibu Kota   

   Total Regencies  Total Cities  Total Districts  Total Urban Villages  \
0                1           5.0               44                 267.0   
1                1           5.0               44                 267.0   
2                1           5.0               44                 267.0   
4                1           5.0               44                 267.0   
6                1           5.0               44                 267.0   

   Total Rural Villages  Area (km2)  Population  Population Density  \
0                   NaN         664    10846145            16334.31   
1                   NaN         664    10846145            16334.31   
2                   NaN         664    10846145            16334.31   
4                   NaN         664    10846145            16334.31   
6                   NaN         664    10846145            16334.31   

    Longitude  Latitude  New Cases per Million  Total Cases per Million  \
0  106.836118 -6.204699                   0.18                     3.60   
1  106.836118 -6.204699                   0.18                     3.78   
2  106.836118 -6.204699                   0.18                     3.96   
4  106.836118 -6.204699                   0.18                     4.15   
6  106.836118 -6.204699                   0.00                     4.15   

   New Deaths per Million  Total Deaths per Million  Total Deaths per 100rb  \
0                    0.00                      1.84                    0.18   
1                    0.00                      1.84                    0.18   
2                    0.00                      1.84                    0.18   
4                    0.00                      1.84                    0.18   
6                    0.09                      1.94                    0.19   

  Case Fatality Rate Case Recovered Rate  Growth Factor of New Cases  \
0             51.28%             192.31%                         NaN   
1             48.78%             182.93%                         1.0   
2             46.51%             174.42%                         1.0   
4             44.44%             166.67%                         1.0   
6             46.67%             166.67%                         0.0   

   Growth Factor of New Deaths  


In [133]:
bandung = jawa [jawa ['City or Regency'] == 'Kota Bandung,']
bandung.head()

Date Location ISO Code    Location  New Cases  New Deaths  \
3  2020-03-03             ID-JB  Jawa Barat          1           1   
5  2020-03-04             ID-JB  Jawa Barat          1           0   
7  2020-03-05             ID-JB  Jawa Barat          1           0   
10 2020-03-06             ID-JB  Jawa Barat          1           0   
13 2020-03-07             ID-JB  Jawa Barat          0           0   

    New Recovered  New Active Cases  Total Cases  Total Deaths  \
3               0                 0            1             1   
5               0                 1            2             1   
7               0                 1            3             1   
10              0                 1            4             1   
13              0                 0            4             1   

    Total Recovered  Total Active Cases Location Level City or Regency  \
3                60                 -60       Province   Kota Bandung,   
5                60                 -59       Province   Kota Bandung,   
7                60                 -58       Province   Kota Bandung,   
10               60                 -57       Province   Kota Bandung,   
13               60                 -57       Province   Kota Bandung,   

      Province    Country Continent Island  Time Zone Special Status  \
3   Jawa Barat  Indonesia      Asia   Jawa  UTC+07:00           None   
5   Jawa Barat  Indonesia      Asia   Jawa  UTC+07:00           None   
7   Jawa Barat  Indonesia      Asia   Jawa  UTC+07:00           None   
10  Jawa Barat  Indonesia      Asia   Jawa  UTC+07:00           None   
13  Jawa Barat  Indonesia      Asia   Jawa  UTC+07:00           None   

    Total Regencies  Total Cities  Total Districts  Total Urban Villages  \
3                18           9.0              627                 645.0   
5                18           9.0              627                 645.0   
7                18           9.0              627                 645.0   
10               18           9.0              627                 645.0   
13               18           9.0              627                 645.0   

    Total Rural Villages  Area (km2)  Population  Population Density  \
3                 5312.0       35378    45161325             1276.55   
5                 5312.0       35378    45161325             1276.55   
7                 5312.0       35378    45161325             1276.55   
10                5312.0       35378    45161325             1276.55   
13                5312.0       35378    45161325             1276.55   

     Longitude  Latitude  New Cases per Million  Total Cases per Million  \
3   107.603708 -6.920432                   0.02                     0.02   
5   107.603708 -6.920432                   0.02                     0.04   
7   107.603708 -6.920432                   0.02                     0.07   
10  107.603708 -6.920432                   0.02                     0.09   
13  107.603708 -6.920432                   0.00                     0.09   

    New Deaths per Million  Total Deaths per Million  Total Deaths per 100rb  \
3                     0.02                      0.02                     0.0   
5                     0.00                      0.02                     0.0   
7                     0.00                      0.02                     0.0   
10                    0.00                      0.02                     0.0   
13                    0.00                      0.02                     0.0   

   Case Fatality Rate Case Recovered Rate  Growth Factor of New Cases  \
3             100.00%            6000.00%                         NaN   
5              50.00%            3000.00%                         1.0   
7              33.33%            2000.00%                         1.0   
10             25.00%            1500.00%                         1.0   
13             25.00%            1500.00%                         0.0   

    Growth Factor of New Deaths  
3           

In [134]:
bandung_case = bandung [['Total Cases','Total Deaths','Total Recovered']].sum()
bandung_case

Total Cases        439196053
Total Deaths         7097250
Total Recovered    412874932
dtype: int64

In [122]:
jakarta_case = jakarta [['Total Cases','Total Deaths','Total Recovered']].sum()
jakarta_case

Total Cases        545806047
Total Deaths         7672746
Total Recovered    526474096
dtype: int64

In [124]:
perbandingan = jakarta [['Total Cases','Total Deaths','Total Recovered']].sum()
print(perbandingan)

explode = [0.08, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
list_value2 = list(perbandingan.values)
list_label2 = list(perbandingan.index)

print(list_value2)
print(list_label2)

Total Cases        545806047
Total Deaths         7672746
Total Recovered    526474096
dtype: int64
[545806047, 7672746, 526474096]
['Total Cases', 'Total Deaths', 'Total Recovered']


In [137]:
perbandingan2 = bandung [['Total Cases','Total Deaths','Total Recovered']].sum()
print(perbandingan2)

explode = [0.08, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
list_value3 = list(perbandingan2.values)
list_label3 = list(perbandingan2.index)

print(list_value3)
print(list_label3)

Total Cases        439196053
Total Deaths         7097250
Total Recovered    412874932
dtype: int64
[439196053, 7097250, 412874932]
['Total Cases', 'Total Deaths', 'Total Recovered']


In [139]:
import plotly.graph_objects as go


fig = go.Figure(data=[
    go.Bar(name='Bandung', x=list_label3, y=list_value3),
    go.Bar(name='Jakarta', x=list_label2, y=list_value2)
])
# Change the bar mode
fig.update_layout(barmode='group')
fig.show()